# Introduction

This is the EDA script for processing the huggingface dataset "zwn22/NC_Crime".

# Durham 

NC State Plane ESPG: 2264 https://epsg.io/2264

In [86]:
import pandas as pd
Durham = pd.read_excel('Durham.xlsx')

## Exploratory Data Analysis

In [87]:
Durham.columns

Index(['Case Number', 'Report Date', 'Report Time', 'Status', 'Sequence',
       'ATT/COM', 'UCR Code', 'Offense', 'Address', 'X', 'Y', 'District',
       'Beat', 'Tract', 'Premise', 'Weapon'],
      dtype='object')

In [2]:
Durham['Weapon'].unique()

array(['(blank)', 'Not Applicable/None', 'Unknown/Not Stated',
       'Personal Weapons', 'Knife/Cutting Instrument', 'Handgun',
       'Blunt Objects', 'Rifle', 'Asphyxiation', 'Other Weapon',
       'Narcotics/Drugs', 'Undetermined Firearm', 'Shotgun',
       'Motor Vehicle/Vessel', 'Fire/Burning Tool/Device',
       'Other Firearm', 'Explosives', 'Poison'], dtype=object)

In [3]:
Durham['Weapon'] = Durham['Weapon'].replace(['(blank)', 'Not Applicable/None', 'Unknown/Not Stated'], None)

In [4]:
Durham['Offense'].unique()

array(['INTIMIDATION', 'FRAUD-IDENTITY THEFT',
       'LARCENY - AUTOMOBILE PARTS OR ACCESSORIES',
       'TOWED/ABANDONED VEHICLE', 'DRUG/NARCOTIC VIOLATIONS',
       'DRUG EQUIPMENT/PARAPHERNALIA', 'MOTOR VEHICLE THEFT', 'BURGLARY',
       'SIMPLE ASSAULT', 'LARCENY - FROM MOTOR VEHICLE',
       'LARCENY - SHOPLIFTING', 'LOST PROPERTY', 'VANDALISM',
       'LARCENY - ALL OTHER', 'DV INFO REPORT (NO CRIME)',
       'ALL OTHER CRIMINAL OFFENSES', 'LARCENY - FROM BUILDING',
       'ALL OTHER OFFENSES-PAROLE/PROBATION VIOLATIONS', 'EMBEZZLEMENT',
       'ASSIST OTHER AGENCY', 'AGGRAVATED ASSAULT',
       'SEX OFFENSE - FORCIBLE RAPE',
       'SEX OFFENSE - SEXUAL ASSAULT WITH AN OBJECT',
       'COUNTERFEITING/FORGERY', 'FRAUD - CONFIDENCE GAMES/TRICKERY',
       'SUSPICIOUS ACTIVITY', 'CALLS FOR SERVICE (NO CRIME)',
       'ROBBERY - COMMERCIAL', 'ROBBERY - INDIVIDUAL',
       'FRAUD - CREDIT CARD/ATM',
       'FRAUD - UNAUTHORIZED USE OF CONVEYANCE', 'RUNAWAY',
       'RECOVERED STOLEN

In [88]:
from pyproj import Transformer

def convert_coordinates(x, y):

    transformer = Transformer.from_crs("epsg:2264", "epsg:4326", always_xy=True)  # 注意设置always_xy=True以保持x,y顺序

    lon, lat = transformer.transform(x, y)
    
    return pd.Series([lat, lon])

In [89]:
# Create a mapping dictionary for crime categories
category_mapping = {
    'Theft': ['LARCENY - AUTOMOBILE PARTS OR ACCESSORIES', 'TOWED/ABANDONED VEHICLE', 'MOTOR VEHICLE THEFT', 'BURGLARY', 'LARCENY - FROM MOTOR VEHICLE', 'LARCENY - SHOPLIFTING', 'LOST PROPERTY', 'VANDALISM', 'LARCENY - ALL OTHER', 'LARCENY - FROM BUILDING', 'RECOVERED STOLEN PROPERTY (OTHER JURISDICTION)', 'LARCENY - POCKET-PICKING', 'LARCENY - FROM COIN-OPERATED DEVICE', 'LARCENY - PURSESNATCHING'],
    'Fraud': ['FRAUD-IDENTITY THEFT', 'EMBEZZLEMENT', 'COUNTERFEITING/FORGERY', 'FRAUD - CONFIDENCE GAMES/TRICKERY', 'FRAUD - CREDIT CARD/ATM', 'FRAUD - UNAUTHORIZED USE OF CONVEYANCE', 'FRAUD - FALSE PRETENSE', 'FRAUD - IMPERSONATION', 'FRAUD - WIRE/COMPUTER/OTHER ELECTRONIC', 'FRAUD - WORTHLESS CHECKS', 'FRAUD-FAIL TO RETURN RENTAL VEHICLE', 'FRAUD-HACKING/COMPUTER INVASION', 'FRAUD-WELFARE FRAUD'],
    'Assault': ['SIMPLE ASSAULT', 'AGGRAVATED ASSAULT'],
    'Drugs': ['DRUG/NARCOTIC VIOLATIONS', 'DRUG EQUIPMENT/PARAPHERNALIA'],
    'Sexual Offenses': ['SEX OFFENSE - FORCIBLE RAPE', 'SEX OFFENSE - SEXUAL ASSAULT WITH AN OBJECT', 'SEX OFFENSE - FONDLING', 'SEX OFFENSE - INDECENT EXPOSURE', 'SEX OFFENSE - FORCIBLE SODOMY', 'SEX OFFENSE - STATUTORY RAPE', 'SEX OFFENSE - PEEPING TOM', 'SEX OFFENSE - INCEST'],
    'Homicide': ['HOMICIDE-MURDER/NON-NEGLIGENT MANSLAUGHTER', 'JUSTIFIABLE HOMICIDE', 'HOMICIDE - NEGLIGENT MANSLAUGHTER'],
    'Arson': ['ARSON'],
    'Kidnapping': ['KIDNAPPING/ABDUCTION'],
    'Weapons Violations': ['WEAPON VIOLATIONS'],
    'Traffic Violations': ['ALL TRAFFIC (EXCEPT DWI)'],
    'Disorderly Conduct': ['DISORDERLY CONDUCT', 'DISORDERLY CONDUCT-DRUNK AND DISRUPTIVE', 'DISORDERLY CONDUCT-FIGHTING (AFFRAY)', 'DISORDERLY CONDUCT-UNLAWFUL ASSEMBLY'],
    'Gambling': ['GAMBLING - OPERATING/PROMOTING/ASSISTING', 'GAMBLING - BETTING/WAGERING'],
    'Animal-related Offenses': ['ANIMAL CRUELTY'],
    'Prostitution-related Offenses': ['PROSTITUTION', 'PROSTITUTION - ASSISTING/PROMOTING', 'PROSTITUTION - PURCHASING']
}

# Function to categorize crime based on the mapping dictionary
def categorize_crime(crime):
    for category, crimes in category_mapping.items():
        if crime in crimes:
            return category
    return 'Miscellaneous'

# Create a new DataFrame with simplified crime categories
Durham_new = pd.DataFrame({
    "year": pd.to_datetime(Durham['Report Date']).dt.year,
    "city": "Durham",
    "crime_major_category": Durham['Offense'].apply(categorize_crime),
    "crime_detail": Durham['Offense'].str.title(),
    "latitude": Durham['X'],
    "longitude": Durham['Y'],
    "occurance_time": pd.to_datetime(Durham['Report Date'] + ' ' + Durham['Report Time']).dt.strftime('%Y/%m/%d %H:%M:%S'),
    "clear_status": Durham['Status'],
    "incident_address": Durham['Address'],
    "notes": Durham['Weapon'].apply(lambda x: f"Weapon: {x}" if pd.notnull(x) else "No Data")
})

Durham_new[['latitude', 'longitude']] = Durham.apply(lambda row: convert_coordinates(row['X'], row['Y']), axis=1).round(5).fillna(0)


In [92]:
Durham_new = Durham_new[Durham_new['year'] >= 2015].fillna("No Data")

In [93]:
Durham_new.tail(5)

year    city crime_major_category  \
149919  2022  Durham                Theft   
149920  2022  Durham        Miscellaneous   
149921  2022  Durham              Assault   
149922  2022  Durham                Theft   
149923  2022  Durham                Fraud   

                                         crime_detail  latitude  longitude  \
149919                   Larceny - From Motor Vehicle  35.88024  -78.85024   
149920  Recovered Stolen Vehicle (Other Jurisdiction)  35.88037  -78.85057   
149921                             Aggravated Assault  35.96519  -78.94559   
149922                                      Vandalism  35.88496  -78.84567   
149923                        Fraud - Credit Card/Atm  35.99019  -78.89111   

             occurance_time          clear_status         incident_address  \
149919  2022/04/13 00:15:00     Cleared By Arrest        5400 S MIAMI BLVD   
149920  2022/04/13 00:15:00     Cleared By Arrest        5400 S MIAMI BLVD   
149921  2022/12/10 01:55:00  Cleared By Exception  3200 OLD CHAPEL HILL RD   
149922  2022/12/31 00:00:00           Active/Open             100 TATUM DR   
149923  2022/05/03 08:36:00     Cleared By Arrest            800 E MAIN ST   

                  notes  
149919  Weapon: (blank)  
149920  Weapon: (blank)  
149921  Weapon: Handgun  
149922  Weapon: (blank)  
149923  Weapon: (blank)

In [94]:
Durham_new.shape

(149922, 10)

# Chapel Hill

In [90]:
import pandas as pd
Chapel = pd.read_csv("Chapel_hill.csv", low_memory=False)

## Exploratory Data Analysis

In [22]:
Chapel.columns

Index(['X', 'Y', 'Incident_ID', 'Agency', 'Offense', 'Street', 'City', 'State',
       'Zipcode', 'Date_of_Report', 'Date_of_Occurrence', 'Date_Found',
       'Reported_As', 'Premise_Description', 'Forcible', 'Weapon_Description',
       'Victim_Age', 'Victim_Race', 'Victim_Gender', 'Latitude', 'Longitude',
       'ObjectId'],
      dtype='object')

In [95]:
Chapel['Reported_As'].unique()

array(['<Null>', 'DISTURBANCE/NUI', 'SUSPICIOUS/WANT', 'TRAFFIC STOP',
       'THEFT/LARCENY', 'MISC OFFICER IN', 'BURGLARY/HOME I',
       'INDECENCY/LEWDN', 'TRAFFIC/TRANSPO', 'MVC W INJURY',
       'DAMAGE/VANDALIS', 'PUBLIC SERVICE', 'TRESPASSING/UNW',
       'INFO MESSAGE', 'HARASSMENT/STAL', 'DOMESTIC DISTUR',
       'ADMINISTRATIVE', 'ELECTRICAL HAZA', 'CARDIAC ARREST',
       'FRAUD OR DECEPT', 'ASSIST CITIZEN', 'ASSAULT/SEXUAL',
       'INTOXICATED SUB', 'LE ASSISTANCE', 'DRUGS', 'SUSPICIOUS OR W',
       'ARREST', 'DISPUTE', 'DISTURBANCE', 'BURGLARY', 'ASSIST OTHR AGE',
       'LARCENY FROM AU', 'TRESPASSING', 'DAMAGE TO PROPE',
       'REFUSAL TO LEAV', 'UNKNOWN PROBLEM', 'WEAPON/FIREARMS',
       'LOUD NOISE', 'ESCORT', 'ABDUCTION/CUSTO', 'VANDALISM',
       'LARCENY OF OTHE', 'LARCENY FROM PE', 'THREATS', 'LARCENY FROM BU',
       'BURGLAR ALARM', 'DOMESTIC', 'CARDIAC RESP AR', 'PROPERTY FOUND',
       'ASSAULT', 'FIREWORKS', 'MISSING/RUNAWAY', 'OVERDOSE',
       'SEXUAL O

In [96]:
Chapel['Weapon_Description'].unique()

array(['<Null>', 'HANDGUN', 'UNKNOWN', 'PERSONAL WEAPONS', 'NONE',
       'SHOTGUN', 'OTHER FIREARM', 'OTHER', 'RIFLE', 'UNARMED',
       'FIREARM (TYP NOT STATED)', 'KNIFE/CUTTING INSTRUMENT',
       'DRUGS/NARCOTICS/SLEEPING PILLS', 'BLUNT OBJECT',
       'FIREARM (TYPE NOT STATED)', 'MOTOR VEHICLE',
       'FIRE/INCENDIARY DEVICE', 'POISON', 'EXPLOSIVES', nan,
       'ASPHYXIATION'], dtype=object)

In [97]:
# Replace specified values with None
replace_values = {'<Null>': None, 'NONE': None}
Chapel['Weapon_Description'] = Chapel['Weapon_Description'].replace(replace_values)

In [98]:
# Create a mapping for crime categories
category_mapping = {
    'Theft': ['THEFT/LARCENY', 'LARCENY FROM AU', 'LARCENY FROM PE', 'LARCENY OF OTHE', 'LARCENY FROM BU', 'LARCENY OF BIKE', 'LARCENY FROM RE', 'LARCENY OF AUTO'],
    'Assault': ['ASSAULT/SEXUAL', 'ASSAULT', 'STAB GUNSHOT PE', 'ACTIVE ASSAILAN'],
    'Burglary': ['BURGLARY', 'BURGLARY ATTEMP', 'STRUCTURE COLLAPSE', 'ROBBERY/CARJACK'],
    'Drugs': ['DRUGS'],
    'Traffic Violations': ['TRAFFIC STOP', 'TRAFFIC/TRANSPO', 'TRAFFIC VIOLATI', 'MVC', 'MVC W INJURY', 'MVC W INJURY AB', 'MVC W INJURY DE', 'MVC ENTRAPMENT'],
    'Disorderly Conduct': ['DISTURBANCE/NUI', 'DOMESTIC DISTUR', 'DISPUTE', 'DISTURBANCE', 'LOST PROPERTY', 'TRESPASSING/UNW', 'REFUSAL TO LEAV', 'SUSPICIOUS COND', 'STRUCTURE FIRE'],
    'Fraud': ['FRAUD OR DECEPT'],
    'Sexual Offenses': ['SEXUAL OFFENSE'],
    'Homicide': ['SUICIDE ATTEMPT', 'ABUSE/ABANDOMEN', 'DECEASED PERSON'],
    'Weapons Violations': ['WEAPON/FIREARMS'],
    'Animal-related Offenses': ['ANIMAL BITE', 'ANIMAL', 'ANIMAL CALL'],
    'Missing Person': ['MISSING PERSON'],
    'Public Service': ['PUBLIC SERVICE', 'PUBLICE SERVICE'],
    'Miscellaneous': ['<Null>', 'SUSPICIOUS/WANT', 'MISC OFFICER IN', 'INDECENCY/LEWDN', 'PUBLIC SERVICE', 'TRESPASSING', 'UNKNOWN PROBLEM', 'LOUD NOISE', 'ESCORT', 'ABDUCTION/CUSTO', 'THREATS', 'BURGLAR ALARM', 'DOMESTIC', 'PROPERTY FOUND', 'FIREWORKS', 'MISSING/RUNAWAY', 'MENTAL DISORDER', 'CHECK WELL BEIN', 'PSYCHIATRIC', 'OPEN DOOR', 'ABANDONED AUTO', 'HARASSMENT THRE', 'JUVENILE RELATE', 'ASSIST MOTORIST', 'HAZARDOUS DRIVI', 'MVC', 'GAS LEAK FIRE', 'ASSIST OTHER AG', 'DOMESTIC ASSIST', 'SUSPICIOUS VEHI', 'UNKNOWN LE', 'ALARMS', '911 HANGUP', 'BOMB/CBRN/PRODU', 'STATIONARY PATR', 'LITTERING', 'HOUSE CHECK', 'CARDIAC', 'CLOSE PATROL', 'BOMB FOUND/SUSP', 'INFO FOR ALL UN', 'UNCONCIOUS OR F', 'LIFTING ASSISTA', 'ATTEMPT TO LOCA', 'SICK PERSON', 'HEAT OR COLD EX', 'CONFINED SPACE', 'TRAUMATIC INJUR', 'DROWNING', 'CITY ORDINANCE']
}


# Function to categorize crime based on the mapping dictionary
def categorize_crime(crime):
    for category, crimes in category_mapping.items():
        if crime in crimes:
            return category
    return 'Miscellaneous'

# Create a new DataFrame with simplified crime categories
Chapel_new = pd.DataFrame({
    "year": pd.to_datetime(Chapel['Date_of_Occurrence']).dt.year,
    "city": "Chapel Hill",
    "crime_major_category": Chapel['Reported_As'].apply(categorize_crime),
    "crime_detail": Chapel['Offense'].str.title(),
    "latitude": Chapel['X'].round(5).fillna(0),
    "longitude": Chapel['Y'].round(5).fillna(0),
    "occurance_time": pd.to_datetime(Chapel['Date_of_Occurrence'].str.replace(r'\+\d{2}$', '', regex=True)).dt.strftime('%Y/%m/%d %H:%M:%S'),
    "clear_status": None,
    "incident_address": Chapel['Street'].str.replace("@", " "),
    "notes": Chapel['Weapon_Description'].apply(lambda x: f"Weapon: {x}" if pd.notnull(x) else "Weapon: None").str.title()
}).fillna("No Data")

Chapel_new = Chapel_new[Chapel_new['year'] >= 2015]
Chapel_new.tail()

year         city crime_major_category                crime_detail  \
101855  2023  Chapel Hill   Disorderly Conduct             Assist Carrboro   
101856  2023  Chapel Hill                Theft  Larceny From Motor Vehicle   
101857  2023  Chapel Hill   Traffic Violations                 Information   
101858  2023  Chapel Hill              Assault        Disturbing The Peace   
101859  2023  Chapel Hill        Miscellaneous               Lost Property   

        latitude  longitude       occurance_time clear_status  \
101855  35.90967  -79.06506  2023/06/24 20:43:00      No Data   
101856  35.92758  -79.03022  2023/09/12 17:45:00      No Data   
101857  35.96392  -79.06455  2023/10/03 15:59:00      No Data   
101858  35.91316  -79.05578  2023/10/27 05:40:00      No Data   
101859  35.91137  -79.06041  2023/05/20 22:30:00      No Data   

                         incident_address                             notes  
101855  W FRANKLIN ST   N MERRITT MILL RD                      Weapon: None  
101856             WILLOW DR   S ESTES DR                      Weapon: None  
101857     WEAVER DAIRY RD EXT PALAFOX DR                      Weapon: None  
101858        W FRANKLIN ST N COLUMBIA ST  Weapon: Knife/Cutting Instrument  
101859                     W FRANKLIN STY                      Weapon: None

In [100]:
Chapel_new.shape

(67010, 10)

# Charlotte

In [101]:
import pandas as pd
Charlotte = pd.read_csv("Charlotte.csv", low_memory = False)

## Exploratory Data Analysis

In [102]:
Charlotte['CLEARANCE_DETAIL_STATUS'].unique()

array(['Open', 'Cleared by Other Means', 'Victim Chose not to Prosecute',
       'Cleared by Arrest', 'Located (Missing Persons and Runaways only)',
       'Unfounded', 'Unfounded-Referred to Other Agency',
       'Cleared, Pending Arrest Validation',
       'Cleared by Arrest by Another Agency',
       'Prosecution Declined by DA', 'By Death of Offender',
       'Extradition Declined'], dtype=object)

In [103]:
Charlotte.columns

Index(['X', 'Y', 'YEAR', 'INCIDENT_REPORT_ID', 'LOCATION', 'CITY', 'STATE',
       'ZIP', 'X_COORD_PUBLIC', 'Y_COORD_PUBLIC', 'LATITUDE_PUBLIC',
       'LONGITUDE_PUBLIC', 'DIVISION_ID', 'CMPD_PATROL_DIVISION', 'NPA',
       'DATE_REPORTED', 'DATE_INCIDENT_BEGAN', 'DATE_INCIDENT_END',
       'ADDRESS_DESCRIPTION', 'LOCATION_TYPE_DESCRIPTION',
       'PLACE_TYPE_DESCRIPTION', 'PLACE_DETAIL_DESCRIPTION',
       'CLEARANCE_STATUS', 'CLEARANCE_DETAIL_STATUS', 'CLEARANCE_DATE',
       'HIGHEST_NIBRS_CODE', 'HIGHEST_NIBRS_DESCRIPTION', 'OBJECTID', 'Shape',
       'GlobalID'],
      dtype='object')

In [104]:
Charlotte['HIGHEST_NIBRS_DESCRIPTION'].unique()

array(['Identity Theft', 'All Other Offenses', 'Theft From Motor Vehicle',
       'Shoplifting', 'All Other Thefts', 'Credit Card/Teller Fraud',
       'Forcible Fondling', 'Damage/Vandalism Of Property',
       'Intimidation', 'Drug/Narcotic Violations',
       'Other Unlisted Non-Criminal', 'Simple Assault',
       'Motor Vehicle Theft', 'Missing Person', 'Embezzlement',
       'Forcible Rape', 'Aggravated Assault', 'Burglary/B&E',
       'Theft From Building', 'Impersonation', 'False Pretenses/Swindle',
       'Extortion/Blackmail', 'Arson', 'Vehicle Recovery', 'Suicide',
       'Sudden/Natural Death Investigation', 'Affray',
       'Weapon Law Violations', 'Trespass Of Real Property', 'Murder',
       'Driving Under The Influence', 'Stolen Property Offenses',
       'Robbery', 'Overdose', 'Theft of Motor Vehicle Parts from Vehicle',
       'Hacking/Computer Invasion', 'Counterfeiting/Forgery',
       'Kidnapping', 'Drug Equipment Violations',
       'Fire (Accidental/Non-Arson)', '

In [128]:
df = Charlotte
df = Charlotte
category_mapping = {
    'Theft': [
        'Identity Theft', 'Theft From Motor Vehicle', 'Shoplifting', 'All Other Thefts',
        'Credit Card/Teller Fraud', 'Motor Vehicle Theft', 'Theft From Building',
        'Theft of Motor Vehicle Parts from Vehicle', 'Purse-Snatching', 'Pocket-Picking',
        'Theft From Coin-Operated Machine Or Device'
    ],
    'Fraud': [
        'Credit Card/Teller Fraud', 'Embezzlement', 'Impersonation', 'False Pretenses/Swindle',
        'Extortion/Blackmail', 'Counterfeiting/Forgery', 'Welfare Fraud', 'Wire Fraud',
        'Hacking/Computer Invasion'
    ],
    'Assault': [
        'Forcible Fondling', 'Simple Assault', 'Aggravated Assault', 'Forcible Rape',
        'Intimidation', 'Sexual Assault With Object', 'Statutory Rape', 'Incest',
        'Forcible Sodomy', 'Affray'
    ],
    'Drugs': [
        'Drug/Narcotic Violations', 'Drug Equipment Violations'
    ],
    'Sexual Offenses': [
        'Forcible Rape', 'Forcible Fondling', 'Sexual Assault With Object',
        'Indecent Exposure', 'Peeping Tom', 'Statutory Rape', 'Incest', 'Forcible Sodomy'
    ],
    'Homicide': [
        'Murder', 'Justifiable Homicide', 'Negligent Manslaughter'
    ],
    'Arson': [
        'Arson', 'Fire (Accidental/Non-Arson)'
    ],
    'Kidnapping': [
        'Kidnapping'
    ],
    'Weapons Violations': [
        'Weapon Law Violations'
    ],
    'Traffic Violations': [
        'Driving Under The Influence'
    ],
    'Disorderly Conduct': [
        'Disorderly Conduct', 'Public Accident'
    ],
    'Gambling': [
        'Assisting Gambling', 'Gambling Equipment Violations', 'Betting/Wagering'
    ],
    'Animal-related Offenses': [
        'Animal Cruelty', 'Dog Bite/Animal Control Incident'
    ],
    'Prostitution-related Offenses': [
        'Prostitution', 'Assisting Prostitution', 'Purchasing Prostitution'
    ]
}

# Function to categorize crime based on the mapping dictionary
def categorize_crime(crime):
    for category, crimes in category_mapping.items():
        if crime in crimes:
            return category
    return 'Miscellaneous'

Charlotte_new = pd.DataFrame({
    "year": df['YEAR'],
    "city": "Charlotte",
    "crime_major_category": df['HIGHEST_NIBRS_DESCRIPTION'].apply(categorize_crime),
    "crime_detail": df['HIGHEST_NIBRS_DESCRIPTION'],
    "latitude": df['LATITUDE_PUBLIC'].round(5).fillna(0),
    "longitude": df['LONGITUDE_PUBLIC'].round(5).fillna(0),
    "occurance_time": pd.to_datetime(df['DATE_INCIDENT_BEGAN'].str.replace(r'\+\d{2}$', '', regex=True), errors='coerce').dt.strftime('%Y/%m/%d %H:%M:%S'),
    "clear_status": df['CLEARANCE_DETAIL_STATUS'],
    "incident_address": df['LOCATION'],
    "notes": 'Location Type Description: ' + df['LOCATION_TYPE_DESCRIPTION'].str.title().str.replace('_', ' ') + '; ' +
             'Place Type Description: ' + df['PLACE_TYPE_DESCRIPTION'].str.title().str.replace('_', ' ') + '; ' +
             'Place Detail Description: ' + df['PLACE_DETAIL_DESCRIPTION'].str.title().str.replace('_', ' ')
})

Charlotte_new.dropna(subset=['occurance_time'], inplace=True)
Charlotte_new.fillna("No Data", inplace=True)
Charlotte_new.tail()

year       city crime_major_category                  crime_detail  \
661137  2017  Charlotte              Assault            Aggravated Assault   
661138  2017  Charlotte        Miscellaneous  Damage/Vandalism Of Property   
661139  2017  Charlotte              Assault                Simple Assault   
661140  2017  Charlotte        Miscellaneous  Damage/Vandalism Of Property   
661141  2017  Charlotte   Disorderly Conduct            Disorderly Conduct   

        latitude  longitude       occurance_time       clear_status  \
661137  35.22712  -80.73457  2017/01/01 00:00:00               Open   
661138  35.25992  -80.89929  2017/01/01 00:00:00               Open   
661139  35.05221  -80.85127  2017/01/01 00:00:00  Cleared by Arrest   
661140  35.26302  -80.84583  2017/01/01 00:00:00               Open   
661141  35.20613  -80.79514  2017/01/01 00:00:00  Cleared by Arrest   

                   incident_address  \
661137             4400 GAYNELLE DR   
661138               1100 MARBLE ST   
661139  14800 BALLANTYNE VILLAGE WY   
661140             2100 KENNESAW DR   
661141       2700 E INDEPENDENCE BV   

                                                    notes  
661137  Location Type Description: Indoors; Place Type...  
661138  Location Type Description: Indoors; Place Type...  
661139  Location Type Description: Outdoors; Place Typ...  
661140  Location Type Description: Indoors; Place Type...  
661141  Location Type Description: Other; Place Type D...

In [129]:
Charlotte_new.shape

(661086, 10)

# Cary

In [107]:
import pandas as pd
Cary = pd.read_csv("Cary.csv", low_memory = False).dropna(subset=['Year'])

## Exploratory Data Analysis

In [108]:
Cary.columns

Index(['Crime Category', 'Crime Type', 'UCR', 'Map Reference',
       'Incident Number', 'Begin Date Of Occurrence',
       'Begin Time Of Occurrence', 'End Date Of Occurrence',
       'End Time Of Occurrence', 'Crime Day', 'Geo Code', 'Location Category',
       'District', 'Beat Number', 'Location', 'ID', 'Lat', 'Lon',
       'Charge Count', 'Neighborhood ID', 'Apartment Complex',
       'Residential Subdivision', 'Subdivision ID', 'Phx Activity Date',
       'Phx Record Status', 'Phx Community', 'Phx Status', 'Record',
       'Offense Category', 'Violent Property', 'timeframe', 'domestic',
       'Total Incidents', 'Year'],
      dtype='object')

In [84]:
Cary['Crime Category'].unique()

array(['ALL OTHER', 'ARSON', 'AGGRAVATED ASSAULT', 'BURGLARY',
       'MOTOR VEHICLE THEFT', 'MURDER', 'ROBBERY', 'LARCENY'],
      dtype=object)

In [110]:
df = Cary
def categorize_crime(crime):
    crime_mapping = {
        'Theft': ['BURGLARY', 'MOTOR VEHICLE THEFT', 'LARCENY'],
        'Arson': ['ARSON'],
        'Assault': ['AGGRAVATED ASSAULT'],
        'Homicide': ['MURDER'],
        'Robbery': ['ROBBERY']
    }

    for category, crimes in crime_mapping.items():
        if crime in crimes:
            return category
    return 'Miscellaneous'

Cary_new = pd.DataFrame({
    "year": df["Year"].astype(int),
    "city": "Cary",
    "crime_major_category": df['Crime Category'].apply(categorize_crime).str.title(),
    "crime_detail": df['Crime Type'].str.title(),
    "latitude": df['Lat'].fillna(0).round(5).fillna(0),
    "longitude": df['Lon'].fillna(0).round(5).fillna(0),
    "occurance_time": pd.to_datetime(df['Begin Date Of Occurrence'] + ' ' + df['Begin Time Of Occurrence']).dt.strftime('%Y/%m/%d %H:%M:%S'),
    "clear_status": None,
    "incident_address": df['Geo Code'],
    "notes": 'District: '+ df['District'].str.title() + 'Violent Property: ' + df['Violent Property'].str.title()
}).fillna("No Data")

Cary_new = Cary_new[Cary_new['year'] >= 2015]
Cary_new.tail()


year  city crime_major_category    crime_detail  latitude  longitude  \
116510  2022  Cary        Miscellaneous  Missing Person  35.79749  -78.81358   
116546  2022  Cary        Miscellaneous  Missing Person  35.78252  -78.81503   
116552  2022  Cary        Miscellaneous  Missing Person  35.76020  -78.74427   
116558  2018  Cary        Miscellaneous  Missing Person  35.82342  -78.90523   
116573  2023  Cary        Miscellaneous  Missing Person  35.78005  -78.75733   

             occurance_time clear_status   incident_address  \
116510  2022/11/13 13:01:36      No Data      EDENHURST AVE   
116546  2022/10/15 15:00:00      No Data     BYRAMS FORD DR   
116552  2022/11/24 12:00:00      No Data          WALNUT ST   
116558  2018/05/10 05:00:00      No Data   EMERALD DOWNS RD   
116573  2023/07/22 23:30:00      No Data  FENTON GATEWAY DR   

                                            notes  
116510  District: CpdnViolent Property: Non-Repor  
116546  District: CpdsViolent Property: Non-Repor  
116552  District: CpdsViolent Property: Non-Repor  
116558    District: D2Violent Property: Non-Repor  
116573  District: CpdsViolent Property: Non-Repor

In [111]:
Cary_new.shape

(44413, 10)

# Raleigh

In [112]:
import pandas as pd

Raleigh = pd.read_csv("Raleigh.csv", low_memory=False)

## Exploratory Data Analysis

In [114]:
Raleigh.columns

Index(['X', 'Y', 'OBJECTID', 'GlobalID', 'case_number', 'crime_category',
       'crime_code', 'crime_description', 'crime_type',
       'reported_block_address', 'city_of_incident', 'city', 'district',
       'reported_date', 'reported_year', 'reported_month', 'reported_day',
       'reported_hour', 'reported_dayofwk', 'latitude', 'longitude', 'agency',
       'updated_date'],
      dtype='object')

In [140]:
# Define category mapping
category_mapping = {
    'Miscellaneous': ['MISCELLANEOUS', 'ALL OTHER OFFENSES'],
    'Sexual Offenses': ['SEX OFFENSES'],
    'Assault': ['ASSAULT', 'SIMPLE ASSAULT'],
    'Juvenile': ['JUVENILE'],
    'Traffic Violations': ['TRAFFIC', 'UNAUTHORIZED MOTOR VEHICLE USE', 'TRAFFIC VIOLATIONS', 'LIQUOR LAW VIOLATIONS'],
    'Fraud': ['FRAUD', 'EMBEZZLEMENT', 'BRIBERY'],
    'Vandalism': ['VANDALISM'],
    'Theft': ['LARCENY FROM MV', 'LARCENY', 'MV THEFT', 'STOLEN PROPERTY'],
    'Burglary': ['BURGLARY/COMMERCIAL', 'BURGLARY/RESIDENTIAL'],
    'Disorderly Conduct': ['DISORDERLY CONDUCT'],
    'Weapons Violations': ['WEAPONS VIOLATION'],
    'Drugs': ['DRUGS', 'DRUG VIOLATIONS'],
    'Arson': ['ARSON'],
    'Robbery': ['ROBBERY'],
    'Kidnapping': ['KIDNAPPING'],
    'Extortion': ['EXTORTION'],
    'Human Trafficking': ['HUMAN TRAFFICKING'],
    'Murder': ['MURDER'],
    'Prostitution-related Offenses': ['PROSTITUTION'],
    'Gambling': ['GAMBLING'],
}

# Function to categorize crime based on the mapping dictionary
def categorize_crime(crime):
    for category, crimes in category_mapping.items():
        if crime in crimes:
            return category
    return 'Miscellaneous'

# Create a new DataFrame with simplified crime categories
Raleigh_new = pd.DataFrame({
    "year": Raleigh['reported_year'],
    "city": "Raleigh",
    "crime_major_category": Raleigh['crime_category'].apply(categorize_crime),
    "crime_detail": Raleigh['crime_description'],
    "latitude": Raleigh['latitude'].round(5).fillna(0),
    "longitude": Raleigh['longitude'].round(5).fillna(0),
    "occurance_time": pd.to_datetime(Raleigh['reported_date'].str.replace(r'\+\d{2}$', '', regex=True), errors='coerce').dt.strftime('%Y/%m/%d %H:%M:%S'),
    "clear_status": None,
    "incident_address": Raleigh['reported_block_address'] + ', ' + Raleigh['district'] + ', Raleigh',
    "notes": 'District: '+ Raleigh['district'].str.title()
}).fillna("No Data")

Raleigh_new = Raleigh_new[Raleigh_new['year'] >= 2015]
# Display the last few rows of the new DataFrame
Raleigh_new.tail()


year     city crime_major_category                   crime_detail  \
496313  2024  Raleigh        Miscellaneous   Pornography/Obscene Material   
496314  2024  Raleigh        Miscellaneous   Pornography/Obscene Material   
496315  2024  Raleigh        Miscellaneous   Pornography/Obscene Material   
496316  2024  Raleigh      Sexual Offenses  Sex Offense/Forcible Fondling   
496317  2024  Raleigh      Sexual Offenses     Sex Offense/Statutory Rape   

        latitude  longitude       occurance_time clear_status  \
496313       0.0        0.0  2024/01/08 12:18:00      No Data   
496314       0.0        0.0  2024/01/08 12:18:00      No Data   
496315       0.0        0.0  2024/01/08 12:19:00      No Data   
496316       0.0        0.0  2024/02/14 21:52:00      No Data   
496317       0.0        0.0  2024/02/14 18:19:00      No Data   

       incident_address                notes  
496313          No Data  District: Northeast  
496314          No Data      District: North  
496315          No Data  District: Southeast  
496316          No Data      District: North  
496317          No Data  District: Northwest

In [141]:
Raleigh_new.shape

(466007, 10)

In [117]:
max(Raleigh_new['latitude'])

35.99118

In [118]:
Raleigh_new['year'].unique()

array([2017, 2016, 2015, 2018, 2019, 2020, 2021, 2022, 2023, 2024])

# Combined

In [142]:
NC = pd.concat([Durham_new, Chapel_new, Charlotte_new, Cary_new, Raleigh_new], ignore_index=True)
NC.head()

year    city crime_major_category  \
0  2022  Durham        Miscellaneous   
1  2019  Durham                Fraud   
2  2020  Durham                Theft   
3  2022  Durham                Theft   
4  2018  Durham                Drugs   

                                crime_detail  latitude  longitude  \
0                               Intimidation  36.03734  -78.87843   
1                       Fraud-Identity Theft  35.90624  -78.90556   
2  Larceny - Automobile Parts Or Accessories  35.98809  -78.88952   
3                    Towed/Abandoned Vehicle  35.92415  -78.78532   
4                   Drug/Narcotic Violations  35.97721  -78.89507   

        occurance_time           clear_status        incident_address  \
0  2022/05/20 12:00:00      Cleared By Arrest        3500 DEARBORN DR   
1  2019/01/01 00:01:00               Inactive  4400 EMERALD FOREST DR   
2  2020/03/09 00:00:00            Active/Open         100 EDGEMONT LN   
3  2022/07/19 10:30:00  Closed (Non-Criminal)  1000 ANDREWS CHAPEL RD   
4  2018/10/18 14:35:00               Inactive           800 DUPREE ST   

                         notes  
0              Weapon: (blank)  
1              Weapon: (blank)  
2              Weapon: (blank)  
3              Weapon: (blank)  
4  Weapon: Not Applicable/None

In [143]:
NC.shape

(1388438, 10)

In [138]:
NC.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1388438 entries, 0 to 1388437
Data columns (total 10 columns):
 #   Column                Non-Null Count    Dtype  
---  ------                --------------    -----  
 0   year                  1388438 non-null  int64  
 1   city                  1388438 non-null  object 
 2   crime_major_category  1388438 non-null  object 
 3   crime_detail          1388438 non-null  object 
 4   latitude              1388438 non-null  float64
 5   longitude             1388438 non-null  float64
 6   occurance_time        1388438 non-null  object 
 7   clear_status          1388438 non-null  object 
 8   incident_address      1388438 non-null  object 
 9   notes                 1388438 non-null  object 
dtypes: float64(2), int64(1), object(7)
memory usage: 105.9+ MB


In [144]:
NC['crime_major_category'].unique()

array(['Miscellaneous', 'Fraud', 'Theft', 'Drugs', 'Assault',
       'Sexual Offenses', 'Traffic Violations', 'Kidnapping',
       'Weapons Violations', 'Homicide', 'Disorderly Conduct', 'Arson',
       'Animal-related Offenses', 'Prostitution-related Offenses',
       'Gambling', 'Public Service', 'Burglary', 'Missing Person',
       'Robbery', 'Juvenile', 'Vandalism', 'Extortion',
       'Human Trafficking', 'Murder'], dtype=object)

In [147]:
NC.to_csv('NC_dataset.csv', index=False)


In [124]:
print(NC.dtypes)

year                      int64
city                     object
crime_major_category     object
crime_detail             object
latitude                float64
longitude               float64
occurance_time           object
clear_status             object
incident_address         object
notes                    object
dtype: object


In [145]:
import numpy as np
np.sort(NC['year'].unique())

array([2015, 2016, 2017, 2018, 2019, 2020, 2021, 2022, 2023, 2024])